## Lab 3.1

In [39]:
import numpy as np
from numpy import pi, sin, exp, log
import plotly.graph_objects as go
import random
import sys
from math import sqrt

😊

Задача - найти минимумы функции f(x, y) с помощью градиентного спуска. 
<br>
Работаем на промежутке X ∈ [-5; 5], Y ∈ [-5: 5], но, если кому хочется, можете расширить :)
<br>
1) Для нахождения всех минимумов нужно будет запускать несколько спусков из случайных точек.
<br>
2) В процессе спуска сохраняйте промежуточные точки (x,y,z) в массивы "путей". Затем пути можно нанести на график с помощью scatter (будет довольно красиво, если дать каждому пути свой цвет).
<br>
3) Нужно заранее подумать о критерии останова для спуска
<br>
4) Спуск тем эффективнее, чем он быстрее. Выделите недостатки алгоритма, предложите(~~украдите~~ найдите или придумайте) какой-нибудь приём(приёмы) для того, чтобы с этими недостатками бороться.


In [40]:
eps = 0.0001

Функция и ее частные производные:

In [41]:
def f(x,y):
    return 10*((x)**5 + pi)*sin(log(((y)**4)+1))/exp(0.8*x**2) + x*5 + 1*(1 - x)**2 - y*2
    #return x**2 + y**2
def df_x(dx, y):
    return (f(dx + eps, y) - f(dx, y)) / eps

def df_y(x, dy):
    return (f(x, dy + eps) - f(x, dy)) / eps

Функция нахождения градиента в точке (x, y):

In [42]:
def gradient(x, y):
    return (df_x(x, y), df_y(x, y))

Сам алгоритм градиентного спуска, ускоренный градиент Нестерова и Среднеквадратичное распространение корня:

In [43]:
max_iterations = sys.maxsize

def gradient_descent(x, y, eps):
    i = 0
    x_i = x
    y_i = y
    z_i = f(x, y)
    path = [[x_i, y_i, z_i]]
    while i < max_iterations:
        x_grad, y_grad = gradient(x_i, y_i)
        k = 0.001
        x_i, y_i = x_i - k * x_grad, y_i - k * y_grad
        z_i = f(x_i, y_i)
        if abs(z_i - path[-1][-1]) <= eps:
            break
        path.append([x_i, y_i, z_i])
        i += 1

    print("Обычный спуск: {} итераций".format(i))
    return path

def gradient_descent_nesterov(x, y, eps):
    i = 0
    x_i = x
    y_i = y
    z_i = f(x, y)
    gamma = 0.9
    vx,vy = gradient(x_i, y_i)
    vx=vx*0.001
    vy=vy*0.001
    path = [[x_i, y_i, z_i]]
    while i < max_iterations:
        x_grad, y_grad = gradient(x_i-gamma*vx, y_i-gamma*vy)
        k = 0.001
        vx,vy=gamma*vx+k*x_grad,gamma*vy+k*y_grad
        x_i, y_i = x_i - vx, y_i - vy
        z_i = f(x_i, y_i)
        if abs(z_i - path[-1][-1]) <= eps:
            break
        path.append([x_i, y_i, z_i])
        i += 1
        
    print("Нестеров: {} итераций".format(i))
    return path

def RMSprop(x, y, eps):
    i = 0
    x_i = x
    y_i = y
    z_i = f(x, y)
    beta = 0.999
    alpha = 0.01
    mx = 0
    my = 0
    path = [[x_i, y_i, z_i]]
    while i < max_iterations:
        x_grad, y_grad = gradient(x_i, y_i)
        mx, my =  mx * beta + (1 - beta) * x_grad**2, my * beta + (1 - beta) * y_grad**2
        x_i = x_i - alpha * x_grad / (sqrt(mx) + eps)
        y_i = y_i - alpha * y_grad / (sqrt(my) + eps)
        z_i = f(x_i, y_i)
        if abs(z_i - path[-1][-1]) <= eps:
            break
        path.append([x_i, y_i, z_i])
        i += 1
        
    print("RMSprop: {} итераций".format(i))
    return path

Получение данных для построения графика функции и метод get_points() - получение случайных точек для запуска из них градиентного спуска:

In [44]:
n_points = 400
x_range = (-5, 5)
y_range = (-5, 5)

X = np.linspace(x_range[0], x_range[1], n_points)
Y = np.linspace(y_range[0], y_range[1], n_points)

Z = np.zeros((n_points, n_points))

for i, x in enumerate(X):
    for j, y in enumerate(Y):
        Z[j][i] = f(x, y)

def get_points():
    return np.random.uniform(-5, 5, (12, 2))


Запуск градиентного спуска и отрисовка графика и путей спусков из случайных точек:

In [45]:
def get_colour():
    rand = lambda: random.randint(100, 255)
    return '#%02X%02X%02X' % (rand(), rand(), rand())


xyz = [go.Surface(z=Z, x=X, y=Y)]    
        
for x, y in get_points():
    path = gradient_descent(x, y, eps)
    path_nesterov = gradient_descent_nesterov(x, y, eps)
    path_adam = RMSprop(x, y, eps)
    paths = np.array(path)
    colour_path = go.Scatter3d(x=paths[:,0],y=paths[:,1],z=paths[:,2], mode='lines+markers', \
                  marker=go.scatter3d.Marker(size=5, color=get_colour()),\
                  line=go.scatter3d.Line(width=5, color=get_colour()))
    xyz.append(colour_path)
    print(path[-1])
    print(path_nesterov[-1])
    print(path_adam[-1])
    
scatter_dict = {
    'x':[0],
    'y':[0],
    'z':[20],
    'mode':'markers',
    'marker':go.scatter3d.Marker(color='green'),
}

fig = go.Figure(data=xyz)
fig.update_layout(title='f(x,y) 3D plot', autosize=False, width=1000, height=1000)

fig.show()

Обычный спуск: 1209 итераций
Нестеров: 174 итераций
RMSprop: 69 итераций
[-1.8766773309980818, 1.4256114837217189, -15.966589824161469]
[-1.8780747684677934, 1.4291761845302107, -15.967283825535498]
[-1.8782765080327541, 1.4296735550844757, -15.967310884222009]
Обычный спуск: 103 итераций
Нестеров: 52 итераций
RMSprop: 25 итераций
[-0.05453101052319642, -3.1936946175548018, -24.0616059916469]
[-0.060517008260700486, -3.2007166608511355, -24.06224083811646]
[-0.056606159516689264, -3.1956192089663404, -24.06223302155259]
Обычный спуск: 1273 итераций
Нестеров: 190 итераций
RMSprop: 35 итераций
[-1.8853081276472663, -1.3657936499595262, -10.377626073749264]
[-1.8779348308334596, -1.3690717006512685, -10.37787949695412]
[-1.882010315862239, -1.3650288720063704, -10.378359726409425]
Обычный спуск: 272 итераций
Нестеров: 82 итераций
RMSprop: 49 итераций
[-0.05171879017633252, -3.1986410572822788, -24.061631469701553]
[-0.05657409594773248, -3.1998770863231245, -24.06248705138313]
[-0.0544906